# TF-IDF

In [50]:
import numpy as np
import pandas as pd
import re
import string
from collections import defaultdict
from sklearn import metrics
from time import time
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from sklearn.datasets import fetch_20newsgroups
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer
import pymorphy2
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, accuracy_score, f1_score

## Загрузка данных

In [7]:
df = pd.read_json('data/healthcare_facilities_reviews.jsonl', lines=True)

In [8]:
df

review_id                       category  \
0              0  Поликлиники стоматологические   
1              1  Поликлиники стоматологические   
2              2  Поликлиники стоматологические   
3              3  Поликлиники стоматологические   
4              4  Поликлиники стоматологические   
...          ...                            ...   
70592      70592          Водительские комиссии   
70593      70593          Водительские комиссии   
70594      70594          Водительские комиссии   
70595      70595          Водительские комиссии   
70596      70596          Водительские комиссии   

                                   title  \
0                        Классный мастер   
1                     Замечательный врач   
2      Благодарность работникам рентгена   
3                       Доктор Рабинович   
4              Есть кому сказать спасибо   
...                                  ...   
70592          Хуже районной поликлиники   
70593                            Справки   
70594       Мед-Альфа - это наше будущее   
70595                  Хамское поведение   
70596         Только хорошие впечатления   

                                                 content sentiment  \
0      Огромное спасибо за чудесное удаление двух зуб...  positive   
1      Хочу выразить особую благодарность замечательн...  positive   
2      Добрый вечер! Хотелось бы поблагодарить сотруд...  positive   
3      Женщины советского образца в регистратуре не и...  negative   
4      У меня с детства очень плохие зубы (тонкая и х...  positive   
...                                                  ...       ...   
70592  Заведение ужасное. Врачи делят 1 кабинет на 2х...  negative   
70593  Люди, не обращайтесь в эту фирму! Муж проходил...  negative   
70594  Дорогие посетители медицинского центра ООО "Ме...  positive   
70595  В регистратуре сидит хамка, такое отношение и ...  negative   
70596  Хочу поблагодарить весь персонал "МедАльфаПроф...  positive   

                                              source_url  
0      http://www.spr.ru/forum_vyvod.php?id_tema=2727539  
1      http://www.spr.ru/forum_vyvod.php?id_tema=2302877  
2      http://www.spr.ru/forum_vyvod.php?id_tema=2815031  
3      http://www.spr.ru/forum_vyvod.php?id_tema=3443161  
4      http://www.spr.ru/forum_vyvod.php?id_tema=2592430  
...                                                  ...  
70592   http://www.spr.ru/forum_vyvod.php?id_tema=273326  
70593  http://www.spr.ru/forum_vyvod.php?id_tema=3401583  
70594   http://www.spr.ru/forum_vyvod.php?id_tema=326078  
70595  http://www.spr.ru/forum_vyvod.php?id_tema=3171911  
70596  http://www.spr.ru/forum_vyvod.php?id_tema=3391562  

[70597 rows x 6 columns]

In [9]:
df = df[['sentiment', 'content']]

In [10]:
df

sentiment                                            content
0      positive  Огромное спасибо за чудесное удаление двух зуб...
1      positive  Хочу выразить особую благодарность замечательн...
2      positive  Добрый вечер! Хотелось бы поблагодарить сотруд...
3      negative  Женщины советского образца в регистратуре не и...
4      positive  У меня с детства очень плохие зубы (тонкая и х...
...         ...                                                ...
70592  negative  Заведение ужасное. Врачи делят 1 кабинет на 2х...
70593  negative  Люди, не обращайтесь в эту фирму! Муж проходил...
70594  positive  Дорогие посетители медицинского центра ООО "Ме...
70595  negative  В регистратуре сидит хамка, такое отношение и ...
70596  positive  Хочу поблагодарить весь персонал "МедАльфаПроф...

[70597 rows x 2 columns]

In [12]:
df['content'][2]

'Добрый вечер! Хотелось бы поблагодарить сотрудников рентгена! Протезируюсь, отношусь к поликлинике № 189. Там меня отфутболили! Подходила к Кочину, зам. гл. врачу, заведующей просто сделать 3 снимка (пол-ка рядом с домом)- мне грубо отказали! А сотрудник рентгена просто сидела кроссворд разгадывала! Они видите ли, не принимают с протезирования! Сказали, где протезируетесь, там и делайте, а я говорю, мне у Вас удобно. Побоялись они! Первый раз попала к молодой девушке, она меня выслушала и сделала 1 снимок, а потом записала на другие дни, мне это удобно. Конечно, народу полно было! Бедные сотрудники. Все, кто читает отзыв (особенно жители Люблино 189 пол-ки), давайте жаловаться в департамент! Спасибо еще раз, за рентген (слышала в очереди, что народу у Вас было много и вы уже перебрали с нормой). Спасибо.'

## Очистка текста

In [25]:
morph = pymorphy2.MorphAnalyzer()
russian_stopwords = stopwords.words("russian")

In [26]:
def clean_text(text):
    # Удаление всего, что не является буквами или знаками препинания
    clean_pattern = re.compile(r'[^a-zA-Zа-яА-ЯёЁ0-9.,!?;:\s]')
    text = clean_pattern.sub('', text)
    url_pattern = re.compile(r'http\S+|www\S+|https\S+')
    text = url_pattern.sub(r'', text)
    text = text.translate(str.maketrans('', '', string.punctuation))
    text = text.lower()
    lemmatized_text =  ' '.join([morph.parse(word)[0].normal_form for word in text.split() if word not in russian_stopwords])
    return lemmatized_text

df['cleaned_text'] = df['content'].apply(clean_text)

/tmp/ipykernel_75887/650983554.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cleaned_text'] = df['content'].apply(clean_text)


In [28]:
df

sentiment                                            content  \
0      positive  Огромное спасибо за чудесное удаление двух зуб...   
1      positive  Хочу выразить особую благодарность замечательн...   
2      positive  Добрый вечер! Хотелось бы поблагодарить сотруд...   
3      negative  Женщины советского образца в регистратуре не и...   
4      positive  У меня с детства очень плохие зубы (тонкая и х...   
...         ...                                                ...   
70592  negative  Заведение ужасное. Врачи делят 1 кабинет на 2х...   
70593  negative  Люди, не обращайтесь в эту фирму! Муж проходил...   
70594  positive  Дорогие посетители медицинского центра ООО "Ме...   
70595  negative  В регистратуре сидит хамка, такое отношение и ...   
70596  positive  Хочу поблагодарить весь персонал "МедАльфаПроф...   

                                            cleaned_text  
0      огромный спасибо чудесный удаление два зуб муд...  
1      хотеть выразить особый благодарность замечател...  
2      добрый вечер хотеться поблагодарить сотрудник ...  
3      женщина советский образец регистратура иметь п...  
4      детство очень плохой зуб тонкий хрупкий эмаль ...  
...                                                  ...  
70592  заведение ужасный врач делить 1 кабинет 2х спе...  
70593  человек обращаться фирма муж проходить анализ ...  
70594  дорогой посетитель медицинский центр ооо медал...  
70595  регистратура сидеть хамка такой отношение мане...  
70596  хотеть поблагодарить весь персонал медальфапро...  

[70597 rows x 3 columns]

In [29]:
df['cleaned_text'][2]

'добрый вечер хотеться поблагодарить сотрудник рентген протезироваться относиться поликлиника 189 отфутболить подходить кочин зам гл врач заведовать просто сделать 3 снимок полка рядом дом грубо отказать сотрудник рентген просто сидеть кроссворд разгадывать видеть принимать протезирование сказать протезироваться делать говорить удобно побояться первый попасть молодой девушка выслушать сделать 1 снимка записать другой день это удобно народ полно бедный сотрудник читать отзыв особенно житель люблино 189 полка давать жаловаться департамент спасибо рентген слышать очередь народ перебрать норма спасибо'

In [34]:
df['sentiment'] = df['sentiment'].apply(lambda x: 1 if x == 'negative' else 0)

/tmp/ipykernel_75887/3526150694.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['sentiment'] = df['sentiment'].apply(lambda x: 1 if x == 'negative' else 0)


In [35]:
df

sentiment                                            content  \
0              0  Огромное спасибо за чудесное удаление двух зуб...   
1              0  Хочу выразить особую благодарность замечательн...   
2              0  Добрый вечер! Хотелось бы поблагодарить сотруд...   
3              1  Женщины советского образца в регистратуре не и...   
4              0  У меня с детства очень плохие зубы (тонкая и х...   
...          ...                                                ...   
70592          1  Заведение ужасное. Врачи делят 1 кабинет на 2х...   
70593          1  Люди, не обращайтесь в эту фирму! Муж проходил...   
70594          0  Дорогие посетители медицинского центра ООО "Ме...   
70595          1  В регистратуре сидит хамка, такое отношение и ...   
70596          0  Хочу поблагодарить весь персонал "МедАльфаПроф...   

                                            cleaned_text  
0      огромный спасибо чудесный удаление два зуб муд...  
1      хотеть выразить особый благодарность замечател...  
2      добрый вечер хотеться поблагодарить сотрудник ...  
3      женщина советский образец регистратура иметь п...  
4      детство очень плохой зуб тонкий хрупкий эмаль ...  
...                                                  ...  
70592  заведение ужасный врач делить 1 кабинет 2х спе...  
70593  человек обращаться фирма муж проходить анализ ...  
70594  дорогой посетитель медицинский центр ооо медал...  
70595  регистратура сидеть хамка такой отношение мане...  
70596  хотеть поблагодарить весь персонал медальфапро...  

[70597 rows x 3 columns]

In [46]:
X_train, X_test, y_train, y_test = train_test_split(df['cleaned_text'], df['sentiment'], test_size=0.2, random_state=42)

## Векторизация и сжатие

In [47]:
vectorizer = TfidfVectorizer(
    max_df=0.9,
    min_df=500,
    # ngram_range=(1, 2),  # Использование униграмм и биграмм
    # max_features=5000,
    stop_words=stopwords.words('russian'),
)
t0 = time()
X_train_tfidf = vectorizer.fit_transform(X_train)
X_test_tfidf = vectorizer.transform(X_test)

print(f"vectorization done in {time() - t0:.3f} s")
print(f"n_samples train: {X_train_tfidf.shape[0]}, n_features: {X_train_tfidf.shape[1]}")
print(f"n_samples test: {X_test_tfidf.shape[0]}, n_features: {X_test_tfidf.shape[1]}")

vectorization done in 4.084 s
n_samples train: 56477, n_features: 1010
n_samples test: 14120, n_features: 1010


In [48]:
lsa = make_pipeline(TruncatedSVD(n_components=500), Normalizer(copy=False))
t0 = time()
X_train_lsa = lsa.fit_transform(X_train_tfidf)

# Применение обученной модели LSA к тестовым данным
X_test_lsa = lsa.transform(X_test_tfidf)
explained_variance = lsa[0].explained_variance_ratio_.sum()

print(f"LSA done in {time() - t0:.3f} s")
print(f"Explained variance of the SVD step: {explained_variance * 100:.1f}%")

LSA done in 14.485 s
Explained variance of the SVD step: 74.3%


## Логистическая регрессия

In [51]:
model = LogisticRegression()

# Обучение модели
model.fit(X_train_lsa, y_train)

# Прогнозирование на тестовой выборке
y_pred = model.predict(X_test_lsa)

# Вывод результатов
print(classification_report(y_test, y_pred))
print(f'Accuracy: {accuracy_score(y_test, y_pred)}')
print(f'F1 score: {f1_score(y_test, y_pred)}')

              precision    recall  f1-score   support

           0       0.94      0.94      0.94      8342
           1       0.91      0.92      0.91      5778

    accuracy                           0.93     14120
   macro avg       0.92      0.93      0.93     14120
weighted avg       0.93      0.93      0.93     14120

Accuracy: 0.9277620396600567
F1 score: 0.9120689655172414


## Создание пайплайна

In [54]:
import re
import pandas as pd
import numpy as np
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import Normalizer
import joblib
import nltk
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer

nltk.download('stopwords')
nltk.download('punkt')

class TextPreprocessor(BaseEstimator, TransformerMixin):
    def __init__(self):
        self.stop_words = set(stopwords.words('russian'))
        self.morph = MorphAnalyzer()

    def preprocess_text(self, text):
        # Удаление всего, что не является буквами или знаками препинания
        clean_pattern = re.compile(r'[^a-zA-Zа-яА-ЯёЁ0-9.,!?;:\s]')
        text = clean_pattern.sub('', text)
        url_pattern = re.compile(r'http\S+|www\S+|https\S+')
        text = url_pattern.sub(r'', text)
        text = text.translate(str.maketrans('', '', string.punctuation))
        text = text.lower()
        tokens = text.split()
        lemmatized_text = ' '.join([self.morph.parse(word)[0].normal_form for word in tokens if word not in self.stop_words])
        return lemmatized_text

    def fit(self, X, y=None):
        return self

    def transform(self, X, y=None):
        return X.apply(self.preprocess_text)


# Load and preprocess the dataset
df = pd.read_json('data/healthcare_facilities_reviews.jsonl', lines=True)
df = df[['sentiment', 'content']]
df['cleaned_text'] = df['content'].apply(TextPreprocessor().preprocess_text)
df['sentiment'] = df['sentiment'].apply(lambda x: 1 if x == 'negative' else 0)

# Split the dataset (this is only for training purposes)
from sklearn.model_selection import train_test_split
train_df, test_df = train_test_split(df, test_size=0.2, random_state=42)

# Create the pipeline
vectorizer = TfidfVectorizer(
    max_df=0.9,
    min_df=500,
    stop_words=stopwords.words('russian')
)

lsa = TruncatedSVD(n_components=500)

pipeline = Pipeline([
    ('preprocessor', TextPreprocessor()),
    ('vectorizer', vectorizer),
    ('lsa', make_pipeline(lsa, Normalizer(copy=False))),
    ('classifier', LogisticRegression())
])

# Train the model
X_train = train_df['cleaned_text']
y_train = train_df['sentiment']
pipeline.fit(X_train, y_train)

# Save the model
# joblib.dump(pipeline, 'logistic_regression_pipeline.pkl')


[nltk_data] Downloading package stopwords to /home/vera/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/vera/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


Pipeline(steps=[('preprocessor', TextPreprocessor()),
                ('vectorizer',
                 TfidfVectorizer(max_df=0.9, min_df=500,
                                 stop_words=['и', 'в', 'во', 'не', 'что', 'он',
                                             'на', 'я', 'с', 'со', 'как', 'а',
                                             'то', 'все', 'она', 'так', 'его',
                                             'но', 'да', 'ты', 'к', 'у', 'же',
                                             'вы', 'за', 'бы', 'по', 'только',
                                             'ее', 'мне', ...])),
                ('lsa',
                 Pipeline(steps=[('truncatedsvd',
                                  TruncatedSVD(n_components=500)),
                                 ('normalizer', Normalizer(copy=False))])),
                ('classifier', LogisticRegression())])

In [55]:
# Save the model for future use
joblib.dump(pipeline, 'logistic_regression_pipeline.pkl')

['logistic_regression_pipeline.pkl']

In [56]:
# Load the model (if not already loaded)
pipeline_test= joblib.load('logistic_regression_pipeline.pkl')

In [61]:
# Sample text for prediction
sample_text = "Ужасная клиника, обслуживание из рук вон плохое, хотеловь бы выразить свое разочарование данным заведением. Советую обходить его мимо."

# Use the pipeline to predict the class
predicted_class = pipeline_test.predict(pd.Series([sample_text]))
predicted_prob = pipeline_test.predict_proba(pd.Series([sample_text]))
print(f"Predicted class: {predicted_class[0]}")
print(f"Predicted proba: {round(predicted_prob[0][1], 3)}")

Predicted class: 1
Predicted proba: 0.898
